# Tranformée de Fourier discrète

## Intro

### pull some data from github

In [ ]:
import os

if not os.path.exists("assets_signal"):
    print("the directory assets_signal is create")
    !git clone https://github.com/vincentvigon/assets_signal
else:
    print("the directory assets_signal is updated")
    %cd assets_signal
    !git pull https://github.com/vincentvigon/assets_signal
    %cd ..


In [ ]:
!pwd

### Import python

In [ ]:
%reset -f
import numpy as np
import matplotlib.pyplot as plt
from IPython.display import Image

np.set_printoptions(linewidth=500,precision=3,suppress=True)

## Rappel sur les séries de Fourier

### Un intervalle continnu

In [ ]:
M=5           #max freq, initial value: 5
N=2*M+1       #nb element in the basis
nb_points=101 #for discretization, initial value: 101

"""we work on a non-symetric interval (why not)"""
left = -1
right = 3
T = right - left

t = np.linspace(left, right,nb_points , endpoint=False)
plt.plot(t,np.zeros_like(t),'+');

### Ranger les ondelettes de $e_{-M}$ à $e_{+M}$

In [ ]:
basis_exp=np.empty([N,len(t)],dtype=np.complex64)

for n in range(-M,+M+1):
    print("creation of the exponential wave corresponding to n=%d"%n)
    basis_exp[M+n,:]=np.exp(2*1j*np.pi*t*n/T)

basis_exp.shape

In [ ]:
fig,axs=plt.subplots(N,2,figsize=(8,N),sharex=True, sharey=True)

for n in range(-M,M+1):
    m=n+M
    axs[m,0].plot(t,np.real(basis_exp[m,:]))
    axs[m,1].plot(t,np.imag(basis_exp[m,:]))

    axs[m,0].set_title("real part, n=%d"%n)
    axs[m,1].set_title("imag part, n=%d"%n)


fig.tight_layout()

### Décomposition d'un signal


In [ ]:
"a signal we want to decompose"
f=(t-1)*(t-3)**2
plt.plot(t,f);

In [ ]:
""" We compute the fourier coef = the coortinates with respect to the expo-basis
alpha[i] =  her(f,basis[i,:]) ~ 1/N sum_j  basis[i,j].conj() f[j] """
alpha = basis_exp.conj()@f /len(t)

In [ ]:
"""we plot the amplitude-spectrum"""
fig,ax=plt.subplots()
ax.plot(range(-M,M+1),np.abs(alpha),".")
ax.set_xticks(range(-M,M+1));

In [ ]:
"""the half amplitude spectrum"""
fig,ax=plt.subplots()
ax.plot(range(0,M+1),np.abs(alpha[M:]),".")
ax.set_xticks(range(0,M+1));

In [ ]:
"""the half amplitude spectrum, with frequencies as x-labels"""
fig,ax=plt.subplots()
ax.plot(range(0,M+1),np.abs(alpha[M:]),".")
ax.set_xticks(range(0,M+1));

frequencies=np.arange(0,M+1)/T
ax.set_xticklabels(frequencies)
ax.set_xlabel("frequencies in Herz");

In [ ]:
""" f_approx[:] = sum_k  alpha[k] basis[k,:]   """
f_approx= alpha@basis_exp

plt.plot(t,f)
plt.plot(t,np.real(f_approx));

***À vous :*** Recommencer toute cette section, mais en changeant les paramètres comme suit :

* tout d'abord, définir `nb_points=11` et conserver `M=5`
* ensuite, définir `M=50` et réinitialiser `nb_points=101`. Dans ce cas, ignorer le dessin de toutes les ondes, c'est trop long.

Dans les deux cas, la matrice `basis_exp` est carrée, et comporte autant de lignes que la taille du signal : donc `f_approx` est égal à `f`. Cela vient simplement du fait que le vecteur `f` peut être exprimé exactement dans la base `basis_exp`.

## Fourier Discret et FFT

Nous allons oublier un instant que les signaux sont indexés par le temps. Nous faisons une approche purement discrète : un signal est simplement un vecteur indexé par des entiers. Nous définissons également nos ondes directement comme des vecteurs.

### Une base de vecteur, indicée de $0$ à $2M+1$


On définit les ondes-exponentielles-discrètes par:
$$
d_n(k)=e^{+2i\pi \frac {nk}N} \qquad k=0,1,...N-1
$$

***Remarque :*** le vecteur $d_n$ est une discrétisation de l'onde exponentielle continue $e_n(t)=e^{+2i\pi \frac {nt}T}$; mais nous gardons ce fait pour plus tard.

In [ ]:
M=4
N=2*M+1
k=np.arange(0,N)

In [ ]:
basis_dis=np.empty([N,N],dtype=np.complex64)
for n in range(N):
    basis_dis[n,:]=np.exp(2*1j*np.pi*n*k/N)

In [ ]:
fig,axs=plt.subplots(N,2,figsize=(8,N),sharex=True,sharey=True)

for n in range(N):
    axs[n,0].plot(k,np.real(basis_dis[n,:]),".")
    axs[n,1].plot(k,np.imag(basis_dis[n,:]),".")

    axs[n,0].set_ylim(-1.1,1.1)
    axs[n,1].set_ylim(-1.1,1.1)

### Orthonormalité

Le produit hermitien naturelle pour notre propos est:
$$
\mathtt{her}(u,v)= \frac 1 N \sum_{n=0}^{N-1} u_n\, \bar v_n
$$
c'est la discrétisation de $\frac 1 T \int_0^T f \bar g$ .


Les coordonnées d'un vecteur $u$ dans cette base sont:
$$
\beta_n= \mathtt{her}(u,d_n) = \sum_{k=0}^{N-1} u_k e^{-2i\pi \frac{nk}N}
$$
(n'oubliez pas le signe moins, qui vient de la conjugaison). Et donc la formule de reconstruction est :
$$
u_k = \sum_{n=0}^{N-1}  \beta_n  e^{+2i\pi \frac{nk}N}
$$

Vocabulaire :

* Les $(\beta_n)$ sont appelés coefficients de Fourier discrets
* Ils sont souvent désignés par $\hat u_n$.
* La transformation $u\to \beta$ est appelée transformée de Fourier discrète.
* La transformation $\beta\to u$ est appelée transformée de Fourier discrète inverse.

On peut aussi écrire la formule de recontruction, sans préciser les indices $k$:
$$
u = \sum_n \beta_n d_n
$$

#### ♡♡♡♡

***A vous :*** Avec python, vérifiez que cette base est orthonormée. Aide : utilisez la multiplication matricielle.

In [ ]:
#--- To keep following outputs, do not run this cell! ---

array([[ 1.+0.j,  0.-0.j,  0.-0.j,  0.-0.j, -0.+0.j, -0.-0.j,  0.+0.j,  0.+0.j,  0.+0.j],
       [ 0.-0.j,  1.+0.j, -0.+0.j,  0.+0.j,  0.-0.j, -0.-0.j, -0.+0.j,  0.+0.j,  0.-0.j],
       [ 0.+0.j,  0.+0.j,  1.+0.j, -0.+0.j,  0.-0.j,  0.-0.j,  0.+0.j,  0.+0.j, -0.-0.j],
       [ 0.+0.j,  0.+0.j,  0.-0.j,  1.+0.j,  0.-0.j,  0.-0.j,  0.+0.j,  0.+0.j, -0.-0.j],
       [ 0.+0.j,  0.+0.j, -0.-0.j,  0.-0.j,  1.+0.j, -0.-0.j, -0.+0.j, -0.-0.j, -0.-0.j],
       [ 0.-0.j, -0.+0.j, -0.+0.j, -0.-0.j, -0.+0.j,  1.-0.j,  0.+0.j, -0.+0.j,  0.-0.j],
       [ 0.+0.j, -0.+0.j,  0.+0.j,  0.+0.j, -0.-0.j,  0.-0.j,  1.-0.j, -0.+0.j,  0.-0.j],
       [ 0.-0.j, -0.+0.j,  0.+0.j,  0.+0.j,  0.+0.j, -0.+0.j, -0.-0.j,  1.+0.j, -0.-0.j],
       [ 0.+0.j,  0.+0.j,  0.-0.j, -0.-0.j,  0.+0.j, -0.-0.j,  0.-0.j,  0.+0.j,  1.-0.j]], dtype=complex64)

### La même base, rangée de $-M$ à $+M$ en passant par zéro



***To you:***  Vérifiez que $d_n=d_{N+n}$ pour tout $n$. En particulier, la famille
$$
d_{-M}, ..., d_0,..., d_{+M}
$$
est une version décallée de
$$
d_0,...,d_{N-1}
$$

#### ♡♡





De plus, comme $e^{-ia}=\overline{e^{ia}}$ on a:
$$
d_{N-n} = d_{-n} = \overline{d_n}
$$



La version décallée $d_{-M}, ..., d_{+M}$ est plus proche de ce que nous avons fait avec les séries de Fourier, mais en pratique c'est bien la version $d_0,...,d_{N-1}$ qui est utilisée.


Mais vous devez vous rappeler que, pour trier les ondes de la plus base fréquence à la plus élevé, il faut regarder les indices en partant de $n=0$. Plus précisémment:


Cas impair: $N=2M+1$:

* $d_0$ qui est constant
* $d_1$ et $d_{N-1}$ qui sont conjugués
* $d_2$ et $d_{N-2}$ qui sont conjugués
* ...
* $d_{M}$ et $d_{M+1}$ qui sont conjugués







Cas par: $N=2M$:

* $d_0$ qui est constant
* $d_1$ et $d_{N-1}$ qui sont conjugués
* $d_{M}$ qui est son propre conjugué, donc c'est un vecteur <font color="red"> □ □ □ </font>.



#### ♡♡♡


$d_M(k)$ a une expression toute simple:



In [ ]:
"""The same basis as before, but puting the constant waves at the middle (as for Fourier-series)"""
basis_dis_dec=np.empty([N,N],dtype=np.complex64)
for n in range(-M,M+1):
    basis_dis_dec[n+M,:]=np.exp(2*1j*np.pi*n*k/N)

In [ ]:
fig,axs=plt.subplots(N,2,figsize=(8,N),sharex=True,sharey=True)

for n in range(N):
    axs[n,0].plot(k,np.real(basis_dis_dec[n,:]),".")
    axs[n,1].plot(k,np.imag(basis_dis_dec[n,:]),".")

    axs[n,0].set_ylim(-1.1,1.1)
    axs[n,1].set_ylim(-1.1,1.1)

### Décomposition en utilisant la FFT


Quelqu'un nous donne un signal échantillonné (=discrétisé). C'est simplement un vecteur : nous ne connaissons même pas la durée originale en secondes. Mais nous pouvons le décomposer en base discrète.


In [ ]:
f2=np.loadtxt("assets_signal/signalToFilter.txt")
N=len(f2)

fig,ax=plt.subplots(figsize=(8,2))
ax.plot(range(N),f2);

In [ ]:
"""We take the basis which has as many elements as the length of the discrete-signal"""
basis_dis=np.empty([N,N],dtype=np.complex128)
x=np.arange(0,N)
for k in range(N):
    basis_dis[k,:]=np.exp(x*2*1j*np.pi*k/N)

In [ ]:
%%time
alpha = basis_dis.conj()@f2 / N


La FFT (Fast Fourier Transform) est un algorithme rapide pour calculer la transformée de Fourier discrète. Elle est récursive : la transformation d'un signal de taille $N$ est réalisée à partir de la décomposition de deux sous-signaux de taille $N/2$. La complexité de la FFT est $N\log(N)$ alors que l'algorithme naturel, qui est une multiplication matricielle, a une complexité de  <font color="red"> □ □ □ </font>



In [ ]:
%%time
alpha_fft=np.fft.fft(f2)

In [ ]:
fig,(ax0,ax1)=plt.subplots(2,1,figsize=(8,4))
ax0.plot(range(N),np.abs(alpha))
ax0.set_title("Fourier coef by oursef")
ax1.plot(range(N),np.abs(alpha_fft))
ax1.set_title("Fourier coef by fft")
fig.tight_layout();

Mais remarquez la différence : `np.fft.fft()` ne divise pas par `N` (voir plus loin).

In [ ]:
%%time
f2_recons= alpha@basis_dis

In [ ]:
%%time
f2_recons_fft=np.fft.ifft(alpha_fft)

In [ ]:
fig,(ax0,ax1)=plt.subplots(2,1,figsize=(8,4))
ax0.plot(range(N),np.abs(f2_recons))
ax0.set_title("signal reconstituated by oursef")
ax1.plot(range(N),np.abs(f2_recons_fft))
ax1.set_title("signal reconstituated by fft")
fig.tight_layout();

### Attention aux conventions
Je choisis de définir les coefficients de Fourier discrets comme
$$
\beta_k=\frac 1 N \sum_{n=0}^{N-1} u_k e^{-2i\pi \frac{nk}N}
$$
Ce qui donne la formule de reconstruction :$$
u_n = \sum_{k=0}^{N-1}  \beta_k  e^{+2i\pi \frac{nk}N}
$$


Mais la plupart des gens définissent
$$
\tilde \beta_k= \sum_{n=0}^{N-1} u_k e^{-2i\pi \frac{nk}N}
$$
Ainsi $\tilde \beta_k$ sont $N$-fois les coordonnées dans la base $(d_n)$ donc la formule de reconstruction devient :
$$
u_n =\frac 1 N \sum_{k=0}^{N-1}  \tilde  \beta_k  e^{+2i\pi \frac{nk}N}
$$

D'autres personnes mettent $\frac 1 {\sqrt{N}}$ devant les deux formules.


### Attention au spectre d'amplitude

La liste des coefficients $(\beta_n)$ est aussi appelée spectre du signal discret et $(|\beta_n|)$ est appelée spectre d'amplitude. Notez que le signal doit être reconstitué à partir du spectre, et non à partir du spectre d'amplitude. Une erreur très courante est de penser que

    ifft(abs(fft(signal))) == signal

Astuce : pour éviter les bugs, je vous conseille de toujours écrire des noms explicites pour votre variable, ex : `amplitude_spectrum`.

## Signaux réels

### Symmétrie Hermitienne

> ***Proposition:*** Soit $u$ un signal discret à valeurs réelles. Ses coefficients de Fourier $\beta$ satisfont
$$
\forall n \in 0,...,N-1:\qquad\beta_{N-n}= \bar \beta_n
$$
**preuve 1 :** (en utilisant la formule de reconstruction)

$$
u_k = \sum_{n=0}^{N-1}  \beta_n  e^{+2i\pi \frac{kn}N}
$$
$$
u = \sum_{n=0}^{N-1}  \beta_n  d_n
$$
Mais parce que $u$ est réel
$$
u = \bar u =  \sum_{n=0}^{N-1}  \bar \beta_n  \bar d_n
$$
en utilisant le fait que $\bar d_n= d_{N-n}$, en utilisant le changement de coordonnée $n \to N-n$ on obtient :
$$
u  =  \sum_{n=0}^{N-1}  \bar \beta_{N-n}  d_n
$$
De l'unicité de la décomposition
$$
\bar \beta_{N-n}= \beta_n
$$
C'est la symétrie hermitienne $\square$

**Preuve 2**, en utilisant la définition des coefficients de Fourier
$$
\beta_n = ... = \beta_{N-n}
$$
 (à compléter)

### Stocker seulement la moitié des coefficients


Lorsque $N=2M+1$, nous ne pouvons calculer et stocker que les quantités $M+1$ suivantes
* $\beta_0$
* $\beta_1 = \bar\beta_{N-1}$
* $\beta_2 = \bar\beta_{N-2}$

$\vdots$

* $\beta_M= \bar \beta_{N-M}=\bar \beta_{M+1}$.

Exemple avec $N=5$

    beta_0   beta_1 beta_2 | beta_3 beta_4

On n'a pas besoin de stocker `beta_3 beta_4`

Lorsque $N=2M$, nous ne pouvons calculer et stocker que les quantités $M+1$ suivantes:
* $\beta_0$
* $\beta_1 = \beta_{N-1}$
* $\beta_2 = \beta_{N-2}$

...

* $\beta_M= \bar \beta_{N-M}=\bar \beta_{M}$, qui est réel


Exemple avec  $N=4$

    beta_0   beta_1 beta_2 | beta_3

On ne stocke pas `beta_3`


La fonction `np.fft.rfft` (la lettre `r` signifie `real`) utilise cette astuce. Elle prend en entrée un signal réel de taille $N$ et donne un signal complexe de taille $N//2+1$ qui est la moitié du spectre. Exemple :

    N → N//2+1
    4 → 3
    5 → 3
    6 → 4
    7 → 4

On voit qu'il y a une difficulté pour la procédure inverse `np.fft.irfft` : l'utilisateur doit préciser la taille initiale du signal pour le récupérer.





In [ ]:
N=4
for N in [4,5]:
    u=np.ones([N])
    beta=np.fft.rfft(u)
    u_back=np.fft.irfft(beta,n=N)
    print(u_back)

***A vous:*** si on ne précise pas `n=N`, que choisi de faire numpy?

### Exemple


In [ ]:
half_spectrum=np.fft.rfft(f2)
"""the size is divided by 2, but it is still complex"""
half_spectrum.shape,half_spectrum.dtype

In [ ]:
fig,ax=plt.subplots(figsize=(8,2))
ax.plot(range(len(half_spectrum)),np.abs(half_spectrum));

In [ ]:
f2_recons_rfft=np.fft.irfft(half_spectrum)
f2_recons_rfft.shape,f2_recons_rfft.dtype

In [ ]:
fig,ax=plt.subplots(figsize=(8,2))
ax.plot(range(len(f2_recons_rfft)),f2_recons_rfft);

## Le retour du temps et des fréquences


### Améliorer le tracé du spectre

Quelqu'un nous dit que le signal précédent a une durée de 2 secondes. Nous pouvons donc ajouter des x-ticks et des x-labels plus informatifs

In [ ]:
f2=np.loadtxt("assets_signal/signalToFilter.txt")
N=len(f2)
T=2

t=np.linspace(0,T,len(f2))
fig,ax=plt.subplots(figsize=(8,2))
ax.plot(t,f2)
ax.set_xlabel("time in second");

Nous voudrions également ajouter des x-ticks plus informatifs sur le spectre : Le choix naturel est : de mettre sous le coef $\beta_n$ la fréquence de l'onde $d_n$ vue comme un échantillonnage d'une onde $t\to e_n(t)$ de $T$-secondes.

### Continuous interpretation of discrete waves

Mais il y a deux choix :
$$
d_n(k)= e_n(t_k) = \overline{ e_{N-n}(t_k) }
$$
avec $t_k= {kT\over N}$

* Pour $n< N/2$ il est plus naturel de voir $d_n$ comme un échantillonnage de $e_n$ qui a pour fréquence $\frac n T$.
* Pour $n>N/2$ il est plus naturel de voir $d_n$ comme un échantillonnage de $\overline{ e_{N-n}}$ qui a pour fréquence $\frac{N-n}T$




In [ ]:
N=10
T=2
basis_dis=np.empty([N,N],dtype=np.complex64)
k=np.arange(0,N)
for n in range(N):
    basis_dis[n,:]=np.exp(2*1j*np.pi*n*k/N)

""" the wave basis_dis[3,:], with the good xlabels """
fig,axs=plt.subplots(N,1,figsize=(N,8))

t=np.linspace(0,T,100)
t_k=np.linspace(0,T,N,endpoint=False)

for n in range(N):
    axs[n].plot(t_k,np.real(basis_dis[n,:]),"o")
    axs[n].plot(t,np.cos(2*np.pi*n*t/T))
    axs[n].plot(t,np.cos(2*np.pi*(N-n)*t/T))

Donc, lorsque $N$ est impair : les différentes fréquences à mettre sous le demi-spectre
$$
\beta_0,\beta_1, ...,\beta_n, ...,\beta_{\frac {N-1} 2}
$$
sont
$$
0, \frac 1 T ,..., \frac {n}T,...,\frac{N-1}{2T}
$$
(et on va jusqu'à $\frac{N}{2T}$ lorsque $N$ est pair).

### Sur notre signal

In [ ]:
f2=np.loadtxt("assets_signal/signalToFilter.txt")
N=len(f2)
T=2

t=np.linspace(0,T,len(f2))
fig,ax=plt.subplots(figsize=(8,2))
ax.plot(t,f2)
ax.set_xlabel("time in second");

In [ ]:
half_spectrum=np.fft.rfft(f2)
frequencies=np.linspace(0,(N-1)/2/T,len(half_spectrum))

fig,ax=plt.subplots(figsize=(8,2))
ax.plot(frequencies,np.abs(half_spectrum))
ax.set_xlabel("frequencies in Hz");

Zoomons

In [ ]:
frequencies_zoom=frequencies[:300]
spectrum_zoom=half_spectrum[:300]

fig,ax=plt.subplots(figsize=(8,2))
ax.plot(frequencies_zoom,np.abs(spectrum_zoom))
ax.set_xlabel("frequencies in Hz");

#### ♡♡♡

***A vous :***  Faites un zoom précisément sur l'intervalle $[0,60Hz]$. Aide : il vous faut donc coder la fonction: fréquence $\to$ index

## Shanon et Nyquist

Lorsque l'on discrétise (=échantillonne) un signal, la fréquence d'échantillonnage est le nombre de points que l'on prend par seconde. Ainsi, l'intervalle entre deux points est l'inverse de la fréquence d'échantillonnage.


Le critère de Shanon indique que, pour réaliser un bon échantillonnage, la fréquence d'échantillonnage doit être deux fois supérieure à la fréquence la plus élevée présente dans le signal (dans sa décomposition en série de Fourier).

Ce théorème est généralement donné avec cette autre formulation : Avec une fréquence d'échantillonnage donnée $\nu$ (ex : 44100Hz), la fréquence la plus élevée que l'on puisse correctement échantillonner est $\frac \nu 2$. Cette fréquence est appelée fréquence de Nyquist.

Observons pourquoi.

### Un signal lisse et son demi-spectre

In [ ]:
"A periodic signal, but only ploted on a bounded interval of T seconds"
def signal(t):
    return np.sin(8*2*np.pi*t)+0.5*np.sin(20*2*np.pi*t)

"""we plot it smoothly"""
T=4    #duration
t_smooth=np.linspace(0,T,1000)
fig,ax=plt.subplots(figsize=(10,1))
signal_smooth=signal(t_smooth)
ax.plot(t_smooth,signal_smooth);

D'après sa définition, la fréquence la plus élevée présente dans ce signal est de $20 Hz$.

In [ ]:
half_amplitude_spectrum=np.abs(np.fft.rfft(signal_smooth))
freqs=np.linspace(0,len(t_smooth)/(2*T),len(half_amplitude_spectrum))
plt.plot(freqs,half_amplitude_spectrum);
plt.xlabel("frequencies in Hz");

### Différents échantillonnages

On garde ce signal, mais on l'échantillonne avec des fréquences d'échantillonnage de plus en plus petites. Il est clair que :

* avec une fréquence d'échantillonnage très élevée (ex : 200) on récupère ce signal juste avec nos yeux.
* avec une fréquence d'échantillonnage très faible (ex : 10) il est impossible d'imaginer le signal d'origine

Il est moins clair que quelque chose change à la fréquence d'échantillonnage $40$Hz qui est le double de la fréquence la plus élevée présente dans le signal.

In [ ]:
sampling_rates=[200,100,50,44,42,40,38,36,20,10]

nb=len(sampling_rates)
fig,axs=plt.subplots(nb,1,figsize=(8,nb),sharex=True)


for i,sampling_rate in enumerate(sampling_rates):
    t=np.linspace(0,T,sampling_rate*T)
    axs[i].plot(t,signal(t),".-")
    axs[i].set_title("sampling rate: %d"%(sampling_rate))

fig.tight_layout()

Observons maintenant le spectre à mi-amplitude. Observez comment la fréquence la plus élevée rebondit à droite lorsque le taux d'échantillonnage passe sous 40Hz.

Lorsque le taux d'échantillonnage est vraiment trop petit, il n'est pas facile de voir lequel des deux pics du spectre dégradé correspond à lequel des deux pics du spectre d'origine. En particulier, à cause de ce rebond, les deux pics peuvent s'additionner, détériorant définitivement l'information. Ce phénomène est appelé 'aliasing' (=repliement ou recouvrement de spectre, en anglais).

In [ ]:
fig,axs=plt.subplots(nb,1,figsize=(8,nb))

for i,sampling_rate in enumerate(sampling_rates):

    t=np.linspace(0,T,sampling_rate*T)
    spectrum=np.abs(np.fft.rfft(signal(t)))/len(t)
    freqs=np.linspace(0,len(t)/(2*T),len(spectrum))
    axs[i].plot(freqs,spectrum,".")
    axs[i].set_title("sampling rate: %d"%(sampling_rate))

fig.tight_layout()

### Explication théorique

Les signaux à temps continu $f$ sur $[0,T]$ peuvent s'écrire :
$$
f(t) = \sum_{j\in \mathbb Z} \alpha_j e^{ 2i\pi \frac {j t} T }
$$
Considérons $u=(u_0,...,u_{N-1})$ un vecteur qui est un échantillonnage de $f$, donc :
$$
u_n = f(n \frac {T}N) \qquad \text{for } n=0,...,N-1
$$
Notons $(\beta_k)$ ses coordonnées dans la base exp discrète de taille $N$ :
$$
u_n = \sum_{k=0}^{N-1} \beta_k e^{2i\pi \frac { k n } N }
$$

Trouvons la relation entre le spectre infini $(\alpha_j)_{j\in \mathbb Z}$ et le spectre fini $(\beta_k)_{k\in 0..N-1}$

\begin{alignat}{1}
u_n = f(n \frac {T}N) &= \sum_{j \in \mathbb Z} \alpha_j \exp ( 2i\pi \frac {j n } N ) \\
&= \sum_{q \in \mathbb Z} \sum_{k=0 }^{N-1} \alpha_{k+qN} \exp ( 2i\pi \frac { (k+qN ) n } N ) \\
&= \sum_{q \in \mathbb Z} \sum_{k=0 }^{N-1} \alpha_{k+qN} \exp ( 2i\pi \frac { k n } N ) \\
&= \sum_{k=0 }^{N-1} \Big( \sum_{q \in \mathbb Z} \alpha_{k+qN} \Big) \exp ( 2i\pi \frac { k n } N ) \\
\end{alignat}

De l'unicité de la décomposition, on obtient :
$$
\beta_k = \Big( \sum_{q \in \mathbb Z} \alpha_{k+qN} \Big)
$$

Interprétation de la formule ci-dessus : Imaginons que le spectre infini $\alpha$ soit une bande de papier où sont imprimés des coefficients. Si on fait rouler cette bande sur elle-même, avec une période $N$, et si on fait la somme des coefficients qui se superposent à cause du roulement, on obtient le spectre fini $\beta$.

Si tous les $\alpha_j$ en dehors de $[-N/2, +N/2]$ sont nuls, cette addition par roulement n'est pas destructive. Mais dans l'autre cas, la sommation peut mélanger les fréquences produisant des repliements. L'information présente sur $f$ ne peut pas être récupérée à partir de $u$.

Bien sûr, tout cela dépend de $N$. Donc, pour éviter le repliement, il faut choisir une fréquence d'échantillonnage suffisamment grande. Pour le son, les fréquences d'échantillonnage vont de 8000 Hz (très, très basse qualité) à 192 000 Hz (très, très haute qualité). Mais la plus courante est 44100 Hz.

***À vous :*** $(1\heartsuit)$ Expliquez pourquoi $44100 Hz$ est un choix raisonnable, sachant que les sons audibles vont de 20 Hz à 20 000 Hz.

***À vous :*** $(2\heartsuit)$ Dans le code précédent, nous voyons un pic du spectre qui rebondit sur la droite, cela est dû à la symétrie hermitienne et au fait que nous ne traçons que le spectre de demi-amplitude. Refaites ce tracé avec le spectre d'amplitude complet pour voir le roulement. Aide : utilisez `np.fft.fft` à la place de `np.fft.rfft`.